In [1]:
import sys
sys.path.append('../')
sys.path.insert(0, '../terrace')

%load_ext autoreload
%autoreload 2

In [50]:
from tqdm import tqdm
import torch.nn.functional as F
from copy import deepcopy
import torch
from common.cfg_utils import get_config
from datasets.make_dataset import *
from models.gnn_bind import *
from models.make_model import *
from common.losses import *
from terrace.batch import *
from terrace.type_data import *
from terrace.comp_node import *


cfg = get_config("../configs", "learnable_ff")
loader = make_dataloader(cfg, "val")
in_node = Input(loader.get_type_data())

In [55]:
F.mse_loss(torch.randn((10,5)), torch.randn((10,5)))

tensor(1.7695)

In [3]:
batch = next(iter(loader))

In [57]:
batch

In [44]:
idx, U = min(list(enumerate(Us)), key=lambda t: t[1])

In [36]:
cfg = get_config("../configs", "learnable_ff")
model = make_model(cfg, in_node)
with torch.no_grad():
    all_lig_coords = model(batch)
all_lig_coords = [ t.detach() for t in all_lig_coords ]

In [38]:
from datasets.graphs.plot_graph import *
lig = batch[0].lig
rec = batch[0].rec
lig_coord = lig.ndata.coord
rec_coord = rec.ndata.coord
lig_coord = lig_coord - lig_coord.mean(0)
rec_coord = rec_coord - rec_coord.mean(0)

pre_rot = torch.randn((3,3), device=lig_coord.device)
trans = torch.randn((3,), device=lig_coord.device)
rot, _ = torch.linalg.qr(pre_rot)
lig_coord = torch.einsum('ij,bj->bi', rot, lig_coord) + trans

lig.ndata.coord = lig_coord
rec.ndata.coord = rec_coord
# plot_graphs([lig, rec])

plot_moving_graph(lig, all_lig_coords, [rec])

In [77]:
rot, _ = torch.linalg.qr(torch.randn((3,3)))
trans = torch.randn(3,)
# torch.linalg.det(rand_rot)
# torch.einsum("ij,jk->ik")
coord = batch.lig.ndata.coord
trans_coord = torch.einsum('ij,bj->bi',rot,coord) + trans

In [78]:
batch_t = deepcopy(batch)
batch_t.lig.ndata.coord = trans_coord

In [81]:
lc_ex = lig_coord.unsqueeze(1).expand(-1,rec_coord.size(0),-1)
rc_ex = rec_coord.unsqueeze(0).expand(lig_coord.size(0),-1,-1)
torch.sqrt(((lc_ex - rc_ex)**2).sum(-1)).shape

torch.Size([63, 54])

In [80]:
lig_coord = batch.lig.ndata.coord
rec_coord = batch.rec.ndata.coord
dists = torch.zeros((lig_coord.shape[0], rec_coord.shape[0]))
for i, lc in enumerate(lig_coord):
    for j, rc in enumerate(rec_coord):
        dists[i,j] = torch.linalg.norm(lc - rc)
dists.shape

torch.Size([63, 54])

In [97]:
mask = torch.zeros((lig_coord.shape[0], rec_coord.shape[0]))
tot_rec = 0
tot_lig = 0
rec_graph = batch.rec.dgl_batch
lig_graph = batch.lig.dgl_batch
for r, l in zip(rec_graph.batch_num_nodes(), lig_graph.batch_num_nodes()):
    mask[tot_lig:tot_lig+l,tot_rec:tot_rec+r] = 1.0
    tot_rec += r
    tot_lig += l
mask

tensor([[1., 1., 1.,  ..., 0., 0., 0.],
        [1., 1., 1.,  ..., 0., 0., 0.],
        [1., 1., 1.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 1., 1., 1.],
        [0., 0., 0.,  ..., 1., 1., 1.],
        [0., 0., 0.,  ..., 1., 1., 1.]])

In [108]:
(1/(torch.cdist(lig_coord, rec_coord))**2)*mask

tensor([[0.0016, 0.0015, 0.0009,  ..., 0.0000, 0.0000, 0.0000],
        [0.0015, 0.0014, 0.0009,  ..., 0.0000, 0.0000, 0.0000],
        [0.0014, 0.0013, 0.0008,  ..., 0.0000, 0.0000, 0.0000],
        ...,
        [0.0000, 0.0000, 0.0000,  ..., 0.0005, 0.0005, 0.0003],
        [0.0000, 0.0000, 0.0000,  ..., 0.0005, 0.0005, 0.0003],
        [0.0000, 0.0000, 0.0000,  ..., 0.0003, 0.0004, 0.0002]])

In [83]:
# from datasets.graphs.plot_graph import *
# plot_graph(batch_t.lig[0])